In [1]:
import warnings
warnings.filterwarnings(action='ignore')
%config Completer.use_jedi = False

In [2]:
from datetime import datetime as dt
import requests
from xml.etree.ElementTree import fromstring, ElementTree
# bulk API를 사용하기 위해 helpers 라이브러리를 import
from elasticsearch import Elasticsearch, helpers
es = Elasticsearch('http://localhost:9200')

서울시 공공와이파이 서비스 개수를 얻어온다.

In [3]:
targetSite = 'http://openapi.seoul.go.kr:8088/746e4968796d6b7639366763624a53/xml/TbPublicWifiInfo/1/1/'
response = requests.get(targetSite)
# print(response.text)
tree = ElementTree(fromstring(response.text)) # 오픈 API가 응답한 XML을 파싱한다.
# print(tree) # <xml.etree.ElementTree.ElementTree object at 0x000001B16D2A9828>
root = tree.getroot() # 파싱된 XML의 root(최상단) 태그(TbPublicWifiInfo)를 얻어온다.
# print(tree.getroot()) # <Element 'TbPublicWifiInfo' at 0x000001B16DCCEC28>
# find('태그이름') 메소드로 파싱된 XML의 특정 태그를 얻어온다.
count = int(root.find('list_total_count').text)
print('{} 현재 서울시가 제공하는 공공와이파이는 모두 {:,d}개 입니다.'.format(dt.now(), count))

2024-06-28 16:35:24.322051 현재 서울시가 제공하는 공공와이파이는 모두 24,587개 입니다.


서울시 공공와이파이 정보를 bulk 데이터로 사용하기 위해 딕셔너리에 저장한다.

In [4]:
docs = [] # bulk 데이터를 저장할 빈 리스트를 선언한다.
idx = 0
for i in range(count // 1000 + 1):
    start = i * 1000 + 1
    end = start + 999
    targetSite = 'http://openapi.seoul.go.kr:8088/746e4968796d6b7639366763624a53/xml/TbPublicWifiInfo/{}/{}/'.format(start, end)
    
    response = requests.get(targetSite)
    tree = ElementTree(fromstring(response.text))
    root = tree.getroot()
    
    for row in root.iter('row'):
        gu = row.find('X_SWIFI_WRDOFC').text
        place = row.find('X_SWIFI_MAIN_NM').text
        lat = row.find('LAT').text
        lon = row.find('LNT').text
        
        doc = {
            '_index': 'seoul_wifi',
            '_source': {
                'gu': gu,
                'place': place,
                'location': {
                    'lat': lat, # 위도
                    'lon': lon  # 경도
                }                
            }
        }
        docs.append(doc) # 엘라스틱서치에 저장할 데이터를 bulk 데이터를 저장할 리스트에 저장한다.
    # ===== for row
    print('종료: {:5d}, {:5d}'.format(start, end))

종료:     1,  1000
종료:  1001,  2000
종료:  2001,  3000
종료:  3001,  4000
종료:  4001,  5000
종료:  5001,  6000
종료:  6001,  7000
종료:  7001,  8000
종료:  8001,  9000
종료:  9001, 10000
종료: 10001, 11000
종료: 11001, 12000
종료: 12001, 13000
종료: 13001, 14000
종료: 14001, 15000
종료: 15001, 16000
종료: 16001, 17000
종료: 17001, 18000
종료: 18001, 19000
종료: 19001, 20000
종료: 20001, 21000
종료: 21001, 22000
종료: 22001, 23000
종료: 23001, 24000
종료: 24001, 25000


--NotebookApp.iopub_data_rate_limit 경고가 발생하면 https://coffee-with-me.tistory.com/16 를 참조한다.

In [5]:
print(docs)

[{'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon':

위도 경도가 뒤바뀐 데이터를 처리한다.

In [6]:
elastic_input = []
for doc in docs:
    # print(doc)
    # print(doc['_source'])
    # print(doc['_source']['location'])
    # print(type(doc['_source']['location']['lat']), doc['_source']['location']['lat'])
    # print(type(doc['_source']['location']['lon']), doc['_source']['location']['lon'])
    # 위도가 경도보다 크면 위도와 경도의 값을 교환한다.
    if float(doc['_source']['location']['lat']) > float(doc['_source']['location']['lon']):
        doc['_source']['location']['lat'], doc['_source']['location']['lon'] = doc['_source']['location']['lon'], doc['_source']['location']['lat']
    elastic_input.append(doc)
print(elastic_input)

[{'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon': '126.96675'}}}, {'_index': 'seoul_wifi', '_source': {'gu': '서대문구', 'place': '상수도사업본부', 'location': {'lat': '37.561924', 'lon':

bulk 데이터를 엘라스틱서치에 인덱싱 한다.

In [7]:
helpers.bulk(es, elastic_input)

(24587, [])